# Постановка задачи

Найдите решение следующей задачи с помощью генетического алгоритма:
$$
y''(x) + \frac{1}{x}y'(x) = - \frac{x^2(1+x)}{x+3}, \;\ x \in [0, \pi],\\
y(0)= 0, \;\ y(\pi) = 0.
$$
Немного преобразуем систему
$$
xy''(x) + y'(x) = - \frac{x^3(1+x)}{x+3}, \;\ x \in [0, \pi],\\
y(0)= 0, \;\ y(\pi) = 0.
$$


# Аналитическое решение

Пусть $y'(x) = z(x).$ Тогда можно получить решение $z(x):$

$$
x(x+3)z'(x) + (x+3)z(x) = -x^3(1+x),\\
z(x) = \frac{c_1}{x} - \frac{x^3}{4} + \frac{2x^2}{3} - 3x + 18 - \frac{54}{x} ln(x+3)
$$

Таким образом необходимо вычислить $y(x) = \int z(x) dx$
$$
y(x) = c_2 + c_1ln(x) - \frac{x^4}{16} + \frac{2x^3}{9} - \frac{3x^2}{2} + 18x - \int \frac{54}{x} ln(x+3)dx
$$

[Проверить можно здесь](https://www.wolframalpha.com/input/?i=x*y%27%27%28x%29+%2B+y%27%28x%29+%3D+-+x%5E3%281%2Bx%29%2F%28x%2B3%29)

# Алгоритм численного решения
Рассмотрим функционал
$$
V(y) = ||Ay - f||^2 = || xy''(x) + y'(x) + \frac{x^3(1+x)}{x+3}||^2 \sim \min_{y}
$$

Введем функцию приспособления $\displaystyle F(y) = \frac{1}{1+V(y)} \in [0,1]$

## Начальная популяция
Начальную популяцию будем генерировать следующим образом:
$$
y_n = \sum_{m=1}^{M} C_m^i f(x,m), \;\ n = 1, ..., N,
$$
где $C_m^i$ и $M$ выбираются случайно. В качестве базисный функций $f(x,m)$ можно взять,например, $sin(mx)$ или $x^m(x-\pi)^m.$

## Отбор

Выберем 
$$y^{n+1}_1 = y^{n}_0: \max_{i} F(y^{n}_i)$$

Выберем порог выживаемости $s$, например,$s = \frac{3}{4}.$ Далее выберем $sN$ функций турнирным отбором:
\begin{equation*}
y^{n+1}_i = 
 \begin{cases}
   y^{n+1}_j, & F(y^{n+1}_j) > F(y^{n+1}_k), \\
   y^{n+1}_k, & F(y^{n+1}_j) \leq F(y^{n+1}_k), \;\ i = 2,..., \frac{3}{4}N.
 \end{cases}
\end{equation*}
где $j,k$ выбраны случайно. Популяция $[sN, N]$ заполняется случайным образом.

Вместо этого можно, например, отранжировать популяцию по значению функции приспособленности и заново сгенерировать $[sN, N]$ функции.

## Выбор родителей

Составляем случайно $N$ пар вида:
$$
y_j^{n+1}, P_j = \frac{F(y_j^{n+1})}{\sum_{i=1}^{N} F(y_i^{n+1})}, \\
y_k^{n+1}, P_k = \frac{F(y_k^{n+1})}{\sum_{i=1}^{N} F(y_i^{n+1})},
$$
где $P_i$ - вероятность выбора $i$-ой функции в качестве родителя. Будем составлять эти пары так, чтобы родители не повторялись

## Скрещивание:
Данным ниже способ скрещивания показался не очень эффективным:
$$
y_i^{n+1} = \frac{F(y_j^{n+1})y_j^{n+1} + F(y_k^{n+1}) y_k^{n+1}}{F(y_j^{n+1}) + F(y_k^{n+1})}
$$

Поэтому был выбран метод промежуточной рекомбинации:
$$
y_i^{n+1} = y_j^{n+1} - \alpha_i(y_k^{n+1} - y_j^{n+1}),
$$
где $\alpha_i$ - коэффициент промежуточной рекомбинации.

# Main

In [1]:
import numpy as np
from math import pi
import sympy as sp
import random

# Визуализация результатов
import plotly.graph_objects as go # Пакет с графикой
from plotly.subplots import make_subplots

In [2]:
N = 50 # Число "особей" в популяции
a, b = 0, pi # Границы переменной x 

x = sp.symbols('x')

In [3]:
class Genetic:
    C = sp.IndexedBase('C')
    
    def __init__(self, N:int, M:int, task=0, mode=0):
        # Размер популяции
        self.N = N
        
        # Выберем задачу и вид базисных функций
        self.task = task # 0 - тест, 1 - поставленная задача
        self.mode = mode # 0 - sin(mx), 1 - x**m*(x-pi)**m, 2 - x**m
        
        # Число базисных функций
        self.M = M
        # Базисные функции
        self.base_functions(self.M)
        
        # Начальная популяция
        self.population = self.get_init_population(N)
        
        
    def base_functions(self, M):
        """ Инициализация базисных функций и функционала"""
        # Инициализируем символьные переменные
        x, m = sp.symbols('x m')
        
        # Выберем базисные функции
        if self.mode == 0: # sin(m*x)
            # Линейная комбинация базисных функций
            s = sp.Sum(self.C[m]*sp.sin(m*x),(m,0,self.M-1)).doit()
            self.base = lambda C: s.subs(C)
        elif self.mode == 1: # x**m*(x-pi)**m
            # Линейная комбинация базисных функций
            s = sp.Sum(self.C[m]*x**m*(x-pi)**m,(m,0,self.M-1)).doit()
            self.base = sp.lambdify(self.C, s)
        elif self.mode == 2: # x**m
            # Линейная комбинация базисных функций
            s = sp.Sum(self.C[m]*x**m,(m,0,self.M-1)).doit()
            self.base = sp.lambdify(self.C, s)
        
            
        # Функционал, который минимизируем
        if self.task == 0:
            V = sp.diff(s,x,2) + 2*sp.sin(x)
        elif self.task == 1:
            V = x*sp.diff(s,x,2) + sp.diff(s,x) + x**3*(1+x)/(x+3)
        self.V = sp.lambdify([self.C, x], V)
        
    
    def fitness(self, C, a, b, num=100):
        """ Вычисление функции приспособления для пробной функции"""
        # Вычислим норму функционала
        V = np.linalg.norm(
                    self.V(C, np.linspace(a, b, num))
        ) ** 2
        
        # Значение функции приспособления
        return 1/(1 + V)
        
    def get_init_population(self, N:int):
        """ Получение начальной популяции"""
        # Инициализируем случайное число базисных функций для каждой пробной функции
        M = np.random.randint(2, self.M, N)
        # Пробные функции будем идентифицировать коэффициентами при базисных функциях
        Cm = np.random.uniform(-2, 2, (N, self.M))
        
        # Инициализируем пустой массив для хранения пробных фугкций и значений функции приспособления
        y = np.array([(None, None) for _ in range(N)])
        
        for n in range(N):
            Cm[n,M[n]:self.M] = 0
            # Пробная функция
            y[n,0] = Cm[n,:]
            # Значение ее функции приспособленности
            y[n,1] = self.fitness(y[n,0], a, b)
        return y

    
    def selection(self, s=1/4):
        """ Отбор функций производится по рейтингу 
        на основании значения функции приспособления
        """
        # Отсортируем по функции приспособления
        self.population = self.population[self.population[:,1].argsort()[::-1]]

        # Число "выживших особей"
        threshold = int(s*N)
        
        # Восстанавливаем популяцию
        self.population[threshold:self.N] = self.get_init_population(self.N-threshold)
        
    
    def crossing(self, d=1/4):
        """ Скрещивание особей в популяции"""        
        # Вероятность особи стать родителем
        tourney_list = self.population[:,1]
        perm = list(tourney_list/np.linalg.norm(tourney_list, ord = 1))
        
        # Сохраним старую популяцию для скрещивания
        y = self.population[:,0].copy()
        
        # Массив с номерами выбранных индексов
        s = set()
        # Очищаем множества от одноэлементных
        bad_sets = {frozenset([n]) for n in range(self.N)}
        # Пока не получим нужное число пар родителей
        while len(s) < self.N:
            # Выбираем согласно вероятности стать родителем 2N пар особей
            s1 = np.random.choice(self.N, (2*self.N,2), p=perm)
            # Убираем пары в которых только один родитель
            s1 = set(map(frozenset,s1)) - bad_sets
            s.update(s1)
        
        # Коэффициент промежуточной рекомбинации
        alpha = (1 + d + d) * np.random.random(self.N) - d    
        
        for n, (j, k) in zip(range(self.N), s):
            # Промежуточная рекомбинация
            self.population[n,0] = y[j] - alpha[n]*(y[k] - y[j])
            # Значение ее функции приспособленности
            self.population[n,1] = self.fitness(self.population[n,0], a, b)
        
    def mutating(self, s=1/2):
        """ Мутирование s доли особей"""
        # Число "мутировавших особей"
        threshold = int(s*self.N)
        
        # Инициализируем случайное число базисных функций для каждой мутации
        M = np.random.randint(2, self.M, threshold)
        # Коэффициенты при базисных функция для каждой мутации
        Cm = np.random.uniform(-0.1, 0.1, (threshold, self.M))
        
        # Для случайности перемешаем популяцию
        np.random.shuffle(gen.population)
        for n in range(threshold):
            Cm[n,M[n]:self.M] = 0
            # Мутация особи
            self.population[n,0] += Cm[n,:]
            # Значение ее функции приспособленности
            self.population[n,1] = self.fitness(self.population[n,0], a, b)

In [4]:
def plot_results(epoch_num, F):
    """Визуализация результатов"""
    
    fig = make_subplots(rows=1, cols=2)
    
    fig.add_trace(go.Heatmap(
        z=F,
        colorscale='Viridis'), 1, 2)
    fig.update_yaxes(title="№ поколения", row=1, col=2)
    fig.update_xaxes(title="популяция", row=1, col=2)
    
    # Построим график зависимости max(F) от номера эпохи
    fig.add_trace(go.Scatter(
            x=np.arange(epoch_num), y=F[:,0], 
            mode='lines',
            name='max F'), 1, 1)
    fig.update_xaxes(title="№ поколения", row=1, col=1)
    fig.update_yaxes(title="max F", row=1, col=1)
        
    # Зазадим размер графика
    fig.update_layout(width=1000, height=800)
    return fig

# Тестовый пример:

Рассмотрим тест:
$$ y''(x) = -2sin(x) \\
y(0)= 0, \;\ y(\pi) = 0
$$

Его решение $\displaystyle y(x) = 2sin(x).$ Выберем базисные функции в виде $sin(mx)$

In [5]:
gen = Genetic(N, 7, 0, 0)
epoch_num = 10

F = np.zeros((epoch_num,N))
for k in range(epoch_num):
    # Отбор
    gen.selection()
    
    # Выведем значение функции приспособленности для лучшей особи
    F[k,:] = gen.population[:,1]
    print(F[k,0])
    
    # Выбор родителей и скрещивание
    gen.crossing()
    
    # Мутация
    gen.mutating()

0.21502370479602428
0.8136335282691585
0.9029162240158811
0.9822594771768751
0.9719343092678737
0.9935958485061563
0.9935294296832083
0.9967112322036651
0.9974829765689198
0.9959803919125821


In [6]:
fig = plot_results(epoch_num, F)
fig.show()

Выведем коэффициенты наилучшей из отобранных функций:
$$C_0sin(0*x) + C_1sin(1*x) + C_2sin(2*x) + ... $$

In [7]:
gen.selection()
replacements = {gen.C[m]: gen.population[0,0][m] for m in range(len(gen.population[0,0]))}
best = gen.base(replacements)
print('score:',gen.population[0,1])
best

score: 0.9997071461522575


2.00121206832752*sin(x) - 0.000527308188986257*sin(2*x)

Рассмотрим второй выбор базисных функций $x^m(x-\pi)^m$. В зависимости от запусков можно преодолеть плато в 0.88

In [8]:
gen = Genetic(N, 7, 0, 1)
epoch_num = 100

F = np.zeros((epoch_num, N))
for k in range(epoch_num):
    # Отбор
    gen.selection()
    
    # Выведем значение функции приспособленности для лучшей особи
    F[k,:] = gen.population[:,1]
    print(F[k,0])
    
    # Выбор родителей и скрещивание
    gen.crossing()
    
    # Мутация
    gen.mutating()

0.02336677623463676
0.031815013463540445
0.07934924720679487
0.10381488241993696
0.2982035650354791
0.19023503909911887
0.24777209448567886
0.2942973765362044
0.41470968670439357
0.5560561597750883
0.6185120354237499
0.7268319239359542
0.820876933867326
0.8258668736005763
0.8437920306411855
0.8575202694790027
0.8790968407919159
0.8846652676303307
0.9009921360163438
0.9068714417613601
0.924301361566776
0.924282613514775
0.9254407219644848
0.9273457868351559
0.9389142978249261
0.950213022938032
0.9725681970927424
0.9866821558323057
0.9889387758776587
0.9919015251443651
0.9931614143876757
0.9959989254740195
0.9959974027073258
0.9976122349775488
0.9981900765239711
0.9984066084465409
0.9983573301822745
0.9984059438364761
0.9984988464768579
0.9987938178659309
0.998647452213988
0.9989002185152549
0.9989186616831098
0.9989954603760752
0.9990773050147546
0.9990782174190318
0.9992882840780655
0.999295740431079
0.9993011017933817
0.999304106170305
0.9993187459115164
0.9993224507862873
0.999333791

In [9]:
fig = plot_results(epoch_num, F)
fig.show()

Выведем коэффициенты наилучшей из отобранных функций:
$$C_0x^0 + C_1x^1 + C_2x^2 + C_3x^3 + C_4x^4 ... $$

In [10]:
gen.selection()
best = sp.expand(gen.base(gen.population[0,0]))
print('score:',gen.population[0,1])
best

score: 0.9996719489669011


-0.0024231020477305*x**6 + 0.0228371987761455*x**5 - 0.00709863151605258*x**4 - 0.33105484533992*x**3 + 0.00118926347518866*x**2 + 2.0007124603121*x + 153.941938205816

# Численный расчет поставленной задачи

- Базисные функции $sin(xm)$ не сходятся за 2к итераций.
- Базисные функции $x^m(x-\pi)^m$ тоже не сходятся за 2к итераций.
- Поэтому расмотрим просто базисные функции $x^m$

В зависимости от случайности значение функции приспособлености может зависнуть на плато в 0.97

In [34]:
gen = Genetic(N, 7, task=1, mode=2)
epoch_num = 500

F = np.zeros((epoch_num, N))
for k in range(epoch_num):
    # Отбор
    gen.selection()
    
    # Выведем значение функции приспособленности для лучшей особи
    F[k,:] = gen.population[:,1]
    print(F[k,0])
    
    # Выбор родителей и скрещивание
    gen.crossing()
    
    # Мутация
    gen.mutating()

0.007157206657406313
0.02594755766227346
0.026323639583005848
0.028664853353440583
0.028514679242663786
0.029162189665268127
0.029263785942370505
0.030255129136384735
0.030090785984941873
0.03075726836548052
0.032830468917113435
0.03329753424106402
0.03389378644641436
0.03450976795578838
0.0346204430960227
0.03476907231411196
0.03486425957778814
0.03503093765886116
0.03502883775247588
0.035080547469429756
0.035103841213958965
0.035110307783253566
0.0351718926747865
0.03570108097591468
0.0357076682964696
0.035838080007472725
0.035855962048810315
0.035915863558640154
0.03591528434138157
0.03591820390395216
0.03592022549958248
0.035921249589852204
0.03592269836301556
0.03592450331836239
0.03592765937523016
0.03593150513358572
0.03593417611863142
0.035936886703792095
0.03593787296539997
0.03593943816024873
0.03593942767359967
0.035939929993640284
0.03594034972487759
0.035944929395001685
0.03594765176608077
0.035949626715190995
0.035950885922591505
0.04742096803643225
0.07620097175877852
0.

0.9707300617993646
0.9707300617993954
0.9707300617994363
0.9707300617995039
0.9707300617995375
0.9707300617995416
0.9707300617995531
0.9707300617995737
0.9707300617996548
0.9707300617996797
0.9707300617997615
0.970730061799845
0.9707300617998783
0.9707300617999268
0.9707300618000105
0.9707300618000779
0.9707300618001174
0.9707300618001371
0.9707300618001681
0.9707300618001854
0.9707300618002216
0.9707300618002511
0.9707300618002648
0.9707300618002757
0.9707300618002866
0.970730061800293
0.9707300618003055
0.9707300618003246
0.9707300618003459
0.9707300618003748
0.9707300618003935
0.9707300618004122
0.9707300618004283
0.9707300618004595
0.9707300618004796
0.9707300618004888
0.9707300618004917
0.9707300618004993
0.9707300618005068
0.9707300618005233
0.9707300618005311
0.970730061800538
0.9707300618005423
0.9707300618005478
0.9707300618005499
0.9707300618005527
0.9707300618005551
0.9707300618005567
0.9707300618005581
0.9707300618005583
0.9707300618005593
0.9707300618005595
0.9707300618005

In [35]:
fig = plot_results(epoch_num, F)
fig.show()

Выведем наилучшую функцию и значение её функции приспособленности (при этом ГУ не удовлетворяются, для этого надо изменить констаты $C_0$ и $C_1$ в соответствии с ГУ)
$$C_0x^0 + C_1x^1 + C_2x^2 + ... $$

In [36]:
gen.selection()
best = sp.expand(gen.base(gen.population[0,0]))
print('score:',gen.population[0,1])
best

score: 0.9707300618005633


-0.0534571353620551*x**4 + 0.0774404486385543*x**3 - 0.102180732829141*x**2 + 0.0667534923208622*x - 9.87679527148747

Коэффициенты $C_0, C_1, ...$

In [37]:
gen.population[0,0]

array([-9.87679527,  0.06675349, -0.10218073,  0.07744045, -0.05345714,
        0.        ,  0.        ])